In [26]:
# !pip install opencv-python
# !pip install moviepy
# !pip install pydub
# !pip install ffmpeg-python

In [1]:
import open_clip
import torch
from PIL import Image

import warnings
from torchaudio import load
# Filter or ignore specific warnings
warnings.filterwarnings("ignore")


torch.manual_seed(42)
torch.cuda.manual_seed(42)

print(torch.__version__)
torch.cuda.is_available()
from PIL import Image

import numpy as np
import transformers
import librosa
from transformers import AutoModelForSpeechSeq2Seq, AutoProcessor, pipeline
from transformers import ClapModel, ClapProcessor, ClapConfig, AutoFeatureExtractor
import os 
device = "cuda:0" if torch.cuda.is_available() else "cpu"
print(device)

/common/home/projectgrps/IS424/IS424G20/jupyterlab-venv-pytorch-py311/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


2.1.2+cu121
cuda:0


In [2]:
model, _, preprocess = open_clip.create_model_and_transforms('xlm-roberta-large-ViT-H-14', 'frozen_laion5b_s13b_b90k')

In [3]:
tokenizer = open_clip.get_tokenizer('xlm-roberta-large-ViT-H-14')

In [4]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print('Using device:', device)
model.to(device)

Using device: cuda


CustomTextCLIP(
  (visual): VisionTransformer(
    (conv1): Conv2d(3, 1280, kernel_size=(14, 14), stride=(14, 14), bias=False)
    (patch_dropout): Identity()
    (ln_pre): LayerNorm((1280,), eps=1e-05, elementwise_affine=True)
    (transformer): Transformer(
      (resblocks): ModuleList(
        (0-31): 32 x ResidualAttentionBlock(
          (ln_1): LayerNorm((1280,), eps=1e-05, elementwise_affine=True)
          (attn): MultiheadAttention(
            (out_proj): NonDynamicallyQuantizableLinear(in_features=1280, out_features=1280, bias=True)
          )
          (ls_1): Identity()
          (ln_2): LayerNorm((1280,), eps=1e-05, elementwise_affine=True)
          (mlp): Sequential(
            (c_fc): Linear(in_features=1280, out_features=5120, bias=True)
            (gelu): GELU(approximate='none')
            (c_proj): Linear(in_features=5120, out_features=1280, bias=True)
          )
          (ls_2): Identity()
        )
      )
    )
    (ln_post): LayerNorm((1280,), eps=1e-05,

In [5]:
a_model = ClapModel.from_pretrained("laion/larger_clap_general").to(device)
a_processor = ClapProcessor.from_pretrained("laion/larger_clap_general")

In [6]:
def getImageFeature(image):
    with torch.no_grad(), torch.cuda.amp.autocast():
        image = preprocess(Image.open(image)).unsqueeze(0)
        image_features = model.encode_image(image.to(device))[0]
    return image_features.cpu().numpy()

def getTextFeature(text):
    with torch.no_grad(), torch.cuda.amp.autocast():
        text = tokenizer(text)
        text_features = model.encode_text(text.to(device))

    return text_features.cpu().numpy()

def getAudioFeature(audio):
    waveform, sample_rate = load(audio)
    inputs = a_processor(audios=waveform.numpy(), return_tensors="pt", sampling_rate=48000).to(device)
    audio_embed = a_model.get_audio_features(**inputs)[0]
    return audio_embed.detach().cpu().numpy()

In [7]:
from inference import MLP

In [8]:
image_model = MLP(dimensions = 1024, number_of_classes = 2,multilabel_bool =False, hidden_dim = 768).to(device)
text_model = MLP(dimensions = 1024, number_of_classes = 2,multilabel_bool =False, hidden_dim = 768).to(device)
audio_model = MLP(dimensions = 512, number_of_classes = 2,multilabel_bool =False, hidden_dim = 768).to(device)

In [9]:
# checkpoint_path = './image_classifier.pth'
checkpoint_path = './new_image_classifier.pth'
loaded_checkpoint = torch.load(checkpoint_path)
image_model.load_state_dict(loaded_checkpoint['model_state_dict'])
image_model.eval()

checkpoint_path = './text_classifier.pth'
loaded_checkpoint = torch.load(checkpoint_path)
text_model.load_state_dict(loaded_checkpoint['model_state_dict'])
text_model.eval()

checkpoint_path = './audio_classifier.pth'
loaded_checkpoint = torch.load(checkpoint_path)
audio_model.load_state_dict(loaded_checkpoint['model_state_dict'])
audio_model.eval()

print("Models Loaded")

Models Loaded


In [10]:
torch_tensor = torch.from_numpy(getImageFeature("horror4929_movie_posters.jpg").reshape(1, -1)).to(device)
desired_dtype = torch.float32
torch_tensor = torch_tensor.to(desired_dtype)
torch_tensor = torch_tensor.unsqueeze(0).to(device)

In [11]:
#Sample Pred
decimal_values = image_model(torch_tensor).cpu().detach().numpy().tolist()
print(decimal_values)

[[0.5471756458282471, 0.45246320962905884]]


In [12]:
torch_tensor = torch.from_numpy(getImageFeature("pos_2179_random human.jpg").reshape(1, -1)).to(device)
desired_dtype = torch.float32
torch_tensor = torch_tensor.to(desired_dtype)
torch_tensor = torch_tensor.unsqueeze(0).to(device)
#negative first, positive
decimal_values = image_model(torch_tensor).cpu().detach().numpy().tolist()
print(decimal_values)

[[0.00368318660184741, 0.9961905479431152]]


### Image-Testing Starts here

In [10]:
import os
import pandas as pd
import matplotlib.pyplot as plt
import pandas as pd
from PIL import Image
def view_image(image_array):
    plt.imshow(image_array)
    plt.axis('off')  # Turn off axis labels
    plt.show()

In [11]:
directory_path = './extra_vid2/cut_Vlad/' #whichever directory you want
files = os.listdir(directory_path)
df = pd.DataFrame({'file': files})

In [12]:
df['label'] = df['file'].apply(lambda x: 'Negative' if x[-5] == '0' else ('Positive' if x[-5] == '1' else 'Unsure'))

In [13]:
df['label'].value_counts()

label
Positive    368
Name: count, dtype: int64

In [14]:
df = df[df['label']!='Unsure']

In [15]:
df = df.reset_index()

#### df['label'].value_counts()

In [18]:
df['predicted'] = ''

#### Video Frames

In [16]:
import vidframes
import cv2
from tqdm import tqdm
from PIL import Image
from IPython.display import display

In [20]:
cd extra_vid2/cut_Vlad/
# cd to which directory that contains your file

/common/home/projectgrps/IS424/IS424G20/extra_vid2/cut_Vlad


In [21]:
# df = df.reset_index()
df = df[['file','label','predicted']]

In [22]:
df['predicted']=""
df['predicted_mean_pool']=""
df

file     label predicted predicted_mean_pool
0              Vlad_50-60_1.mp4  Positive                              
1            Vlad_270-280_1.mp4  Positive                              
2            Vlad_120-130_1.mp4  Positive                              
3    Family_Guy_1280-1290_1.mp4  Positive                              
4    Family_Guy_1590-1600_1.mp4  Positive                              
..                          ...       ...       ...                 ...
363  Family_Guy_2070-2080_1.mp4  Positive                              
364          Vlad_580-590_1.mp4  Positive                              
365    Family_Guy_740-750_1.mp4  Positive                              
366    Family_Guy_770-780_1.mp4  Positive                              
367    Family_Guy_500-510_1.mp4  Positive                              

[368 rows x 4 columns]

In [37]:
# cd to directory with your video files

In [25]:
for index, file_name in tqdm(enumerate(df['file']), total=len(df['file']), desc="Processing files"):
    try:
        frames = vidframes.extract(file_name)   
        classification = []
        stacked_features = []
        for frame in frames:
            processed_frame = preprocess(Image.fromarray(frame)).unsqueeze(0)
            image_features = model.encode_image(processed_frame.to(device))[0]
            image_features = image_features.reshape(1, -1)
            stacked_features.append(image_features)
            output = image_model(image_features)
            predicted_class = torch.argmax(output, 1)
            classification.append(int(predicted_class[0]))
 
        stacked_features = torch.stack(stacked_features, dim=0)
        mean_pooled_features = torch.mean(stacked_features, dim=0)
        output = image_model(mean_pooled_features)
        predicted_class2 = torch.argmax(output, 1)

        df.at[index, 'predicted_mean_pool'] = int(predicted_class2[0])
              
        df.at[index, 'predicted'] = classification

    except Exception as e:
        print(e)
        print(file_name)

Processing files:   2%|█                                                                | 6/368 [00:07<06:13,  1.03s/it][h264 @ 0x18b8b580] mmco: unref short failure
[h264 @ 0x18b8b580] mmco: unref short failure
Processing files:   2%|█▌                                                               | 9/368 [00:09<05:36,  1.07it/s][h264 @ 0x173677c0] mmco: unref short failure
[h264 @ 0x173677c0] mmco: unref short failure
[h264 @ 0x173677c0] mmco: unref short failure
[h264 @ 0x173677c0] mmco: unref short failure
Processing files:   3%|█▋                                                              | 10/368 [00:11<06:04,  1.02s/it][h264 @ 0x1c2b0e80] mmco: unref short failure
[h264 @ 0x1c2b0e80] mmco: unref short failure
Processing files:   5%|███▏                                                            | 18/368 [00:18<06:11,  1.06s/it][h264 @ 0x18c1e480] mmco: unref short failure
[h264 @ 0x18c1e480] mmco: unref short failure
[h264 @ 0x18c1e480] mmco: unref short failure
[h264 @ 0x18c1

In [23]:
df['predicted_label']=""

In [24]:
import numpy as np
df['predicted_label'] = df['predicted'].apply(lambda x: np.mean(x))

In [25]:
df

file     label                 predicted  \
0        Conjuring2_7.5-8.0_1.mp4  Positive  [0, 0, 0, 0, 0, 0, 0, 0]   
1       Halloween_93.0-93.5_0.mp4  Negative  [0, 0, 0, 0, 0, 0, 0, 0]   
2      Conjuring2_37.5-38.0_0.mp4  Negative     [0, 0, 0, 0, 0, 0, 0]   
3    Condor_Hero2_17.5-18.0_1.mp4  Positive  [1, 1, 1, 1, 1, 1, 1, 1]   
4    Condor_Hero2_11.5-12.0_1.mp4  Positive     [1, 1, 1, 1, 0, 1, 1]   
..                            ...       ...                       ...   
323       Halloween_7.0-7.5_0.mp4  Negative  [0, 0, 0, 0, 0, 0, 0, 0]   
324  Condor_Hero1_13.0-13.5_1.mp4  Positive     [1, 1, 1, 1, 1, 1, 1]   
325    Conjuring2_47.0-47.5_0.mp4  Negative  [0, 0, 0, 0, 0, 0, 0, 0]   
326    Condor_Hero1_6.0-6.5_1.mp4  Positive  [1, 1, 1, 1, 1, 1, 1, 1]   
327  Condor_Hero1_23.5-24.0_1.mp4  Positive  [1, 1, 1, 1, 1, 1, 1, 1]   

    predicted_mean_pool  predicted_label  
0                     0         0.000000  
1                     0         0.000000  
2                     0         0.000000  
3                     1         1.000000  
4                     1         0.857143  
..                  ...              ...  
323                   0         0.000000  
324                   1         1.000000  
325                   0         0.000000  
326                   1         1.000000  
327                   1         1.000000  

[328 rows x 5 columns]

In [44]:
threshold = 0.5
df['predicted_label'] = np.where(df['predicted_label'] >= threshold, 'Positive', 'Negative')

In [33]:
df.to_csv('image_results.csv')

In [46]:
for index, row in df.iterrows():
    predicted_values = row['predicted']

    # Compute the mean of the 'predicted' values
    mean_predicted = sum(predicted_values) / len(predicted_values)

    # Update the 'predicted_mean' column
    df.at[index, 'predicted_mean'] = mean_predicted

In [47]:
for index, row in df.iterrows():
    if row['predicted_mean']>=0.50:
        df.at[index, 'predicted_binary'] = 'Positive'
    else:
        df.at[index, 'predicted_binary'] = 'Negative'

In [49]:
df.to_csv('review_cv.csv')

#### Audio

In [17]:
model_id = "openai/whisper-large-v3"
model_asr = AutoModelForSpeechSeq2Seq.from_pretrained(
    model_id, torch_dtype=torch.float32, use_safetensors=True
)
processor = AutoProcessor.from_pretrained(model_id)
model_asr.to('cuda')

pipe = pipeline(
    "automatic-speech-recognition",
    model=model_asr,
    tokenizer=processor.tokenizer,
    feature_extractor=processor.feature_extractor,
    max_new_tokens=128,
    chunk_length_s=30,
    batch_size=1,
    return_timestamps=False, 
    torch_dtype=torch.float32,
    device=0,
)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


#### Extract Audio ASR and Audio Embeddings

In [18]:
from moviepy.video.io.VideoFileClip import VideoFileClip
from pydub import AudioSegment
import numpy as np
from audio_separator.separator import Separator
import os
import warnings

# Suppress all warnings
warnings.filterwarnings("ignore")


In [19]:
separator = Separator()
separator.load_model()

INFO:audio_separator.separator.separator:Separator version 0.13.1 instantiating with output_dir: None, output_format: WAV
DEBUG:audio_separator.separator.separator:Normalization threshold set to 0.9, waveform will lowered to this max amplitude to avoid clipping.
DEBUG:audio_separator.separator.separator:Denoising disabled, model will only be run once. This is twice as fast, but may result in noisier output audio.
DEBUG:audio_separator.separator.separator:Separation settings set: sample_rate=44100, hop_length=1024, segment_size=256, overlap=0.25, batch_size=1
INFO:audio_separator.separator.separator:Checking hardware specifics to configure acceleration
INFO:audio_separator.separator.separator:Operating System: Linux #1 SMP Wed Nov 29 18:55:19 UTC 2023
INFO:audio_separator.separator.separator:System: Linux Node: toga Release: 4.18.0-513.9.1.el8_9.x86_64 Machine: x86_64 Proc: x86_64
INFO:audio_separator.separator.separator:Python Version: 3.11.4
INFO:audio_separator.separator.separator:ON

In [21]:
df['text']=""

In [34]:
cd ../

/common/home/projectgrps/IS424/IS424G20


In [53]:
primary_stem_path

'temp_audio_(Vocals)_UVR-MDX-NET-Inst_HQ_3.wav'

In [26]:
cd ../

/common/home/projectgrps/IS424/IS424G20


In [22]:
df['text_pred']=""
df['audio_pred']=""

In [25]:
audio_path = "./temp_audio.wav"

for index, file_name in tqdm(enumerate(df['file'].iloc[0:], 0), total=len(df['file'].iloc[0:]), desc="Processing files"):
    try:
        video_path ="extra_vid2/cut_Vlad/"+file_name
        video_clip = VideoFileClip(video_path)
        video_clip.audio.write_audiofile(audio_path, codec="pcm_s16le", ffmpeg_params=["-ac", "1"])
        primary_stem_path, secondary_stem_path = separator.separate('temp_audio.wav')
        result = pipe('temp_audio.wav')
        torch_tensor = torch.from_numpy(getTextFeature(result['text'])[0]).reshape(1, -1).to(device)
        desired_dtype = torch.float32
        torch_tensor = torch_tensor.to(desired_dtype)
        torch_tensor = torch_tensor.unsqueeze(0).to(device)
        predicted_class_text = int(torch.argmax(text_model(torch_tensor), 1)[0])
        predicted_class_audio = int(torch.argmax(audio_model(torch.from_numpy(getAudioFeature(secondary_stem_path).reshape(1, -1)).to(device)),dim=1)[0])

        df.at[index, 'text_pred'] = predicted_class_text
        df.at[index, 'text'] = result['text']
        df.at[index, 'audio_pred'] = predicted_class_audio
        

    except Exception as e:
        print(e)
        print(file_name)


Processing files:   0%|                                                                         | 0/368 [00:00<?, ?it/s]

MoviePy - Writing audio in ./temp_audio.wav



Processing files:   0%|                                                                         | 0/368 [00:00<?, ?it/s]INFO:audio_separator.separator.separator:Starting separation process for audio_file_path: temp_audio.wav
DEBUG:audio_separator.separator.separator:Preparing mix...
DEBUG:audio_separator.separator.separator:Loading audio from file: temp_audio.wav


MoviePy - Done.


DEBUG:audio_separator.separator.separator:Audio loaded. Sample rate: 44100, Audio shape: (499653,)
DEBUG:audio_separator.separator.separator:Audio file is valid and contains data.
DEBUG:audio_separator.separator.separator:Mix is mono. Converting to stereo.
DEBUG:audio_separator.separator.separator:Converted to stereo mix.
DEBUG:audio_separator.separator.separator:Mix preparation completed.
DEBUG:audio_separator.separator.separator:Normalizing mix before demixing...
DEBUG:audio_separator.separator.separator:Maximum peak amplitude not above clipping threshold, no need to normalize: 0.77215576171875
DEBUG:audio_separator.separator.separator:Starting demixing process with is_match_mix: False...
DEBUG:audio_separator.separator.separator:Initializing model settings...
DEBUG:audio_separator.separator.separator:Model input params: n_fft=6144 hop_length=1024 dim_f=3072
DEBUG:audio_separator.separator.separator:Model settings: n_bins=3073, trim=3072, chunk_size=261120, gen_size=254976
DEBUG:audi

...

DEBUG:audio_separator.separator.separator:Model run on the spectrum without denoising.
DEBUG:audio_separator.separator.separator:Inverse STFT applied. Returning result with shape: (1, 2, 261120)
DEBUG:audio_separator.separator.separator:Processing chunk 2/3: Start 195840, End 456960
DEBUG:audio_separator.separator.separator:Window applied to the chunk.
DEBUG:audio_separator.separator.separator:Mix part split into batches. Number of batches: 1
DEBUG:audio_separator.separator.separator:Processing mix_wave batch 1/1
DEBUG:audio_separator.separator.separator:STFT applied on mix. Spectrum shape: torch.Size([1, 4, 3072, 256])
DEBUG:audio_separator.separator.separator:Model run on the spectrum without denoising.
DEBUG:audio_separator.separator.separator:Inverse STFT applied. Returning result with shape: (1, 2, 261120)
DEBUG:audio_separator.separator.separator:Processing chunk 3/3: Start 391680, End 516096
DEBUG:audio_separator.separator.separator:Window applied to the chunk.
DEBUG:audio_separ

MoviePy - Writing audio in ./temp_audio.wav



Processing files: 100%|██████████████████████████████████████████████████████████████▊| 367/368 [16:51<00:03,  3.06s/it]INFO:audio_separator.separator.separator:Starting separation process for audio_file_path: temp_audio.wav
DEBUG:audio_separator.separator.separator:Preparing mix...
DEBUG:audio_separator.separator.separator:Loading audio from file: temp_audio.wav
DEBUG:audio_separator.separator.separator:Audio loaded. Sample rate: 44100, Audio shape: (470106,)
DEBUG:audio_separator.separator.separator:Audio file is valid and contains data.
DEBUG:audio_separator.separator.separator:Mix is mono. Converting to stereo.
DEBUG:audio_separator.separator.separator:Converted to stereo mix.
DEBUG:audio_separator.separator.separator:Mix preparation completed.
DEBUG:audio_separator.separator.separator:Normalizing mix before demixing...
DEBUG:audio_separator.separator.separator:Maximum peak amplitude not above clipping threshold, no need to normalize: 0.529449462890625
DEBUG:audio_separator.separa

MoviePy - Done.


DEBUG:audio_separator.separator.separator:Model run on the spectrum without denoising.
DEBUG:audio_separator.separator.separator:Inverse STFT applied. Returning result with shape: (1, 2, 261120)
DEBUG:audio_separator.separator.separator:Processing chunk 2/3: Start 195840, End 456960
DEBUG:audio_separator.separator.separator:Window applied to the chunk.
DEBUG:audio_separator.separator.separator:Mix part split into batches. Number of batches: 1
DEBUG:audio_separator.separator.separator:Processing mix_wave batch 1/1
DEBUG:audio_separator.separator.separator:STFT applied on mix. Spectrum shape: torch.Size([1, 4, 3072, 256])
DEBUG:audio_separator.separator.separator:Model run on the spectrum without denoising.
DEBUG:audio_separator.separator.separator:Inverse STFT applied. Returning result with shape: (1, 2, 261120)
DEBUG:audio_separator.separator.separator:Processing chunk 3/3: Start 391680, End 516096
DEBUG:audio_separator.separator.separator:Window applied to the chunk.
DEBUG:audio_separ

In [28]:
df.to_csv('newest_preds2.csv')

In [5]:
df = pd.read_csv('newest_preds.csv')